<h1>Содержание<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Подготовка" data-toc-modified-id="Подготовка-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Подготовка</a></span></li><li><span><a href="#Анализ" data-toc-modified-id="Анализ-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Анализ</a></span></li><li><span><a href="#Обучение" data-toc-modified-id="Обучение-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Обучение</a></span></li><li><span><a href="#Тестирование" data-toc-modified-id="Тестирование-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Тестирование</a></span></li><li><span><a href="#Чек-лист-проверки" data-toc-modified-id="Чек-лист-проверки-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Чек-лист проверки</a></span></li></ul></div>

#  Прогнозирование заказов такси

Компания «Чётенькое такси» собрала исторические данные о заказах такси в аэропортах. Чтобы привлекать больше водителей в период пиковой нагрузки, нужно спрогнозировать количество заказов такси на следующий час. Постройте модель для такого предсказания.

Значение метрики *RMSE* на тестовой выборке должно быть не больше 48.

Вам нужно:

1. Загрузить данные и выполнить их ресемплирование по одному часу.
2. Проанализировать данные.
3. Обучить разные модели с различными гиперпараметрами. Сделать тестовую выборку размером 10% от исходных данных.
4. Проверить данные на тестовой выборке и сделать выводы.


Данные лежат в файле `taxi.csv`. Количество заказов находится в столбце `num_orders` (от англ. *number of orders*, «число заказов»).

## Подготовка

### Загрузка необходимых библиотек

In [2]:
%pip install cufflinks

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


### Импорт библиотек

In [3]:
# импорты из стандартной библиотеки
import time
import warnings

# импорты сторонних библиотек
import cufflinks as cf
import numpy as np
import pandas as pd
import seaborn as sns

# импорты модулей текущего проекта
from catboost import CatBoostClassifier, CatBoostRegressor, Pool, cv
from lightgbm import LGBMRegressor
from sklearn.compose import make_column_transformer
from sklearn.linear_model import Ridge
from sklearn.metrics import make_scorer, mean_absolute_error, mean_squared_error
from sklearn.model_selection import (
    GridSearchCV,
    RandomizedSearchCV,
    cross_val_score,
    train_test_split,
)
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler
from sklearn.tree import DecisionTreeRegressor
from statsmodels.tsa.seasonal import seasonal_decompose

# настройки
warnings.filterwarnings("ignore")

# константы заглавными буквами
RANDOM_STATE = 1504

cf.go_offline()
cf.set_config_file(world_readable=True, theme='pearl', offline=True)

### Загрузка данных

In [4]:
try:
    orders = pd.read_csv("/datasets/taxi.csv", index_col=[0], parse_dates=[0])
except:
    orders = pd.read_csv("https://code.s3.yandex.net/datasets/taxi.csv", index_col=[0], parse_dates=[0])

In [5]:
orders.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 26496 entries, 2018-03-01 00:00:00 to 2018-08-31 23:50:00
Data columns (total 1 columns):
 #   Column      Non-Null Count  Dtype
---  ------      --------------  -----
 0   num_orders  26496 non-null  int64
dtypes: int64(1)
memory usage: 414.0 KB


In [6]:
def check_df(df):
    print("СВОДНАЯ ИНФОРМАЦИЯ О ДАТАФРЕЙМЕ")
    print(
        "******************************"
    )
    print("===ОБЩАЯ ИНФОРМАЦИЯ===")
    display(df.info())
    print(
        "******************************"
    )
    print("===ПЕРВЫЕ 5 СТРОК ДАТАФРЕЙМА===")
    display(df.head(5))
    print(
        "******************************"
    )
    print("===СТАТИСТИКА===")
    display(df.describe())
    print(
        "******************************"
    )
    print("===ПРОПУЩЕННЫЕ ЗНАЧЕНИЯ===")
    print(df.isna().sum())
    print(
        "******************************"
    )
    print("===ВРЕНЕННОЙ ИНТЕРВАЛ===")
    print(f'Начало интервала: {df.index.min()}')
    print(f'Конец интервала: {df.index.max()}')
    print(
        "******************************"
    )
    print("===ГРАФИЧЕСКОЕ ПРЕДСТАВЛЕНИЕ===")
    df.sort_index(inplace=True)
    df.iplot(kind='scatter',xTitle='dates',yTitle='num_orders')

In [7]:
check_df(orders)

СВОДНАЯ ИНФОРМАЦИЯ О ДАТАФРЕЙМЕ
******************************
===ОБЩАЯ ИНФОРМАЦИЯ===
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 26496 entries, 2018-03-01 00:00:00 to 2018-08-31 23:50:00
Data columns (total 1 columns):
 #   Column      Non-Null Count  Dtype
---  ------      --------------  -----
 0   num_orders  26496 non-null  int64
dtypes: int64(1)
memory usage: 414.0 KB


None

******************************
===ПЕРВЫЕ 5 СТРОК ДАТАФРЕЙМА===


num_orders
datetime                       
2018-03-01 00:00:00           9
2018-03-01 00:10:00          14
2018-03-01 00:20:00          28
2018-03-01 00:30:00          20
2018-03-01 00:40:00          32

******************************
===СТАТИСТИКА===


num_orders
count  26496.000000
mean      14.070463
std        9.211330
min        0.000000
25%        8.000000
50%       13.000000
75%       19.000000
max      119.000000

******************************
===ПРОПУЩЕННЫЕ ЗНАЧЕНИЯ===
num_orders    0
dtype: int64
******************************
===ВРЕНЕННОЙ ИНТЕРВАЛ===
Начало интервала: 2018-03-01 00:00:00
Конец интервала: 2018-08-31 23:50:00
******************************
===ГРАФИЧЕСКОЕ ПРЕДСТАВЛЕНИЕ===


### Предварительный анализ

Итак, что мы имеем:
1. Набор данных, состоящий из 26 496 записей, с одним признаком `num_orders` и индексом, содержащим временной ряд;
1. `num_orders` имеет тип данных int64, который в данном случае явно избыточен.
1. Данные взяты за период с 01.03.2018 по 31.08.2018, с 00:00 до 23:50 соответственно.
1. В данных отсутствуют пропуски;
1. Осуществлять проверку на наличие дубликатов бессмыссленно, т.к. кол-во заказов может повторятся и это нормально.


В целом данные хорошие, осталось только сделать пару штрихов:

1. Ресемплировать данные по одному часу
1. Преобразовать тип данных признака `num_orders`, применив к нему метод downcast;

In [8]:
# Ресемплируем данные по одному часу
orders = orders.resample('1H').sum()

In [9]:
# Преобразовываем тип данных num_orders
orders.num_orders = pd.to_numeric(orders.num_orders, downcast="integer")
orders.num_orders.dtype

dtype('int16')

In [10]:
check_df(orders)

СВОДНАЯ ИНФОРМАЦИЯ О ДАТАФРЕЙМЕ
******************************
===ОБЩАЯ ИНФОРМАЦИЯ===
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 4416 entries, 2018-03-01 00:00:00 to 2018-08-31 23:00:00
Freq: H
Data columns (total 1 columns):
 #   Column      Non-Null Count  Dtype
---  ------      --------------  -----
 0   num_orders  4416 non-null   int16
dtypes: int16(1)
memory usage: 43.1 KB


None

******************************
===ПЕРВЫЕ 5 СТРОК ДАТАФРЕЙМА===


num_orders
datetime                       
2018-03-01 00:00:00         124
2018-03-01 01:00:00          85
2018-03-01 02:00:00          71
2018-03-01 03:00:00          66
2018-03-01 04:00:00          43

******************************
===СТАТИСТИКА===


num_orders
count  4416.000000
mean     84.422781
std      45.023853
min       0.000000
25%      54.000000
50%      78.000000
75%     107.000000
max     462.000000

******************************
===ПРОПУЩЕННЫЕ ЗНАЧЕНИЯ===
num_orders    0
dtype: int64
******************************
===ВРЕНЕННОЙ ИНТЕРВАЛ===
Начало интервала: 2018-03-01 00:00:00
Конец интервала: 2018-08-31 23:00:00
******************************
===ГРАФИЧЕСКОЕ ПРЕДСТАВЛЕНИЕ===


### Вывод

Данные были загруженны и проанализированны. В результате анализа было произведено ресемплированние данных и понижена разрядность числового типа данных признака `num_orders` для уменьшения ресурсозатрат при обучении модели.

Данные готовы к дальнейшему исследованию.

## Анализ

Еще раз взглянем на график наших данных:

In [11]:
orders.iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Orders",
)

Выполним декомпозицию данных, применив функцию `seasonal_decompose()`, чтобы лучше проанализировать данные:

In [12]:
decomposed_orders = seasonal_decompose(orders) 

Оценим общий тренд:

In [13]:
decomposed_orders.trend.iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Trend",
)

График растет. Количество вызовов такси в аэропорт летом вырастает. Можно предположить, что это аэропорт какого-то курортного города.

Посмотрим поближе крайние 2 недели:

In [14]:
decomposed_orders.trend.last('2W').iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Trend",
)

Видим, что количество заказов не равномерно в течении недели. В начале недели наблюдается спад, который переходит в к концу недели.

Теперь оценим сезонную составляющую:

In [15]:
decomposed_orders.seasonal.iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Seasonal",
)

Аж зарябило в глазах, попробуем взять только последнюю неделю:

In [16]:
decomposed_orders.seasonal.last("1W").iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Seasonal",
)

Мы видим, что пик нагрузки приходится на полночь, но затем количество заказов пададает вплоть до 06:00, после чего снова начинает расти. Очевидно, что это связано с ночными рейсами. 

Посмотрим на остатки декомпозиции:

In [17]:
decomposed_orders.resid.iplot(
    kind="scatter",
    xTitle="dates",
    yTitle="num_orders",
    title="Residuals",
)

Дисперсия увеличивается со временем, наиболее хорошо это заметно во второй половине августа

### Вывод

Проведя анализ данных определим признаки, которые нам понадобятся для обучения наших моделей:

1. `hour` - ночью такси вызывают активнее, значит время вызова имеет значение
1. `day` - поскольку, в середине недели заказов меньше, чем в выходные.
1. `dayofweek` - аналогично предыдущему - интенсивность заказов в течение недели скачет.
1. `month` - тренд растет от месяца к месяцу, этот признак нам понадобится

## Обучение

Для обучения выберем 4 модели:
1. Ridge
2. DecisionTree
3. CatBoostRegressor
4. LightGBMRegressor

Напишем функцию для создания необходимых признаков:

In [18]:
def make_features(df, max_lag, rolling_mean_size):
    # календарные фичи
    df.month = df.index.month
    df.day = df.index.day
    df.dayofweek = df.index.dayofweek
    df.hour = df.index.hour

    # "отстающие" фичи
    for lag in range(1, max_lag + 1):
        df[f'lag_{lag}'] = df.num_orders.shift(lag)

    # "скользящее среднее"
    df.rolling_sum = df.num_orders.shift().rolling(rolling_mean_size).mean()

Применим нашу функцию и посмотрим на результат

In [19]:
make_features(orders, 24, 4)
orders.head(5)

num_orders  lag_1  lag_2  lag_3  lag_4  lag_5  lag_6  \
datetime                                                                    
2018-03-01 00:00:00         124    NaN    NaN    NaN    NaN    NaN    NaN   
2018-03-01 01:00:00          85  124.0    NaN    NaN    NaN    NaN    NaN   
2018-03-01 02:00:00          71   85.0  124.0    NaN    NaN    NaN    NaN   
2018-03-01 03:00:00          66   71.0   85.0  124.0    NaN    NaN    NaN   
2018-03-01 04:00:00          43   66.0   71.0   85.0  124.0    NaN    NaN   

                     lag_7  lag_8  lag_9  ...  lag_15  lag_16  lag_17  lag_18  \
datetime                                  ...                                   
2018-03-01 00:00:00    NaN    NaN    NaN  ...     NaN     NaN     NaN     NaN   
2018-03-01 01:00:00    NaN    NaN    NaN  ...     NaN     NaN     NaN     NaN   
2018-03-01 02:00:00    NaN    NaN    NaN  ...     NaN     NaN     NaN     NaN   
2018-03-01 03:00:00    NaN    NaN    NaN  ...     NaN     NaN     NaN     NaN   
2018-03-01 04:00:00    NaN    NaN    NaN  ...     NaN     NaN     NaN     NaN   

                     lag_19  lag_20  lag_21  lag_22  lag_23  lag_24  
datetime                                                             
2018-03-01 00:00:00     NaN     NaN     NaN     NaN     NaN     NaN  
2018-03-01 01:00:00     NaN     NaN     NaN     NaN     NaN     NaN  
2018-03-01 02:00:00     NaN     NaN     NaN     NaN     NaN     NaN  
2018-03-01 03:00:00     NaN     NaN     NaN     NaN     NaN     NaN  
2018-03-01 04:00:00     NaN     NaN     NaN     NaN     NaN     NaN  

[5 rows x 25 columns]

Подготовим выборки для обучения моделей:

In [20]:
train, test = train_test_split(orders, shuffle=False, test_size=0.1)
train = train.dropna()

In [21]:
X_train = train.drop('num_orders', axis = 1)
y_train = train.num_orders
X_test = test.drop('num_orders', axis = 1)
y_test = test.num_orders

In [22]:
print(f'Размер обучающей выборки: {X_train.shape[0]}')
print(f'Размер тестовой выборки: {X_test.shape[0]}')

Размер обучающей выборки: 3950
Размер тестовой выборки: 442


### Обучение моделей

#### Ridge

In [23]:
%%time
# random_state не перебирается, задаём его прямо в модели
model_ridge = Ridge(random_state=RANDOM_STATE)

# словарь с гиперпараметрами и значениями, которые хотим перебрать
param_grid_ridge = {
    'alpha': np.arange(0, 0.21, 0.01),
}

# ищем лучшие гиперпараметры
gs_ridge = GridSearchCV(
    model_ridge, 
    param_grid=param_grid_ridge, 
    scoring='neg_root_mean_squared_error', 
    n_jobs=-1
)

# обучаем модель
gs_ridge.fit(X_train, y_train)

# получаем лучше значение метрики при помощи кросс-валидации,
# чтобы избежать предсказаний на валидационной выборке
gs_ridge_best_score = (
    cross_val_score(
        gs_ridge.best_estimator_,
        X_train,
        y_train,
        cv=5,
        scoring="neg_mean_squared_error",
    ).mean()* -1) ** 0.5

gs_ridge_best_params = gs_ridge.best_params_
gs_ridge_fit_time = gs_ridge.cv_results_['mean_fit_time'][gs_ridge.best_index_]
gs_ridge_predict_time = gs_ridge.cv_results_['mean_score_time'][gs_ridge.best_index_]

print(f"best_params: {gs_ridge_best_params}")
print('------------------------------')
print(f"best_score: {gs_ridge_best_score}")
print(f"gs_ridge_fit_time: {gs_ridge_fit_time}")
print(f"gs_ridge_predict_time: {gs_ridge_predict_time}")


best_params: {'alpha': 0.2}
------------------------------
best_score: 26.256635051282885
gs_ridge_fit_time: 0.005198860168457031
gs_ridge_predict_time: 0.002599477767944336
CPU times: total: 391 ms
Wall time: 4.43 s


#### DecisionTreeRegressor

In [24]:
%%time

model_dt = DecisionTreeRegressor(random_state=RANDOM_STATE)

param_grid_dt = {
    "max_depth": range(2, 15),
    "min_samples_split": (2, 3, 4),
    "min_samples_leaf": (1, 2, 3, 4),
}

gs_dt = RandomizedSearchCV(
    model_dt,
    param_distributions=param_grid_dt,
    scoring="neg_root_mean_squared_error",
    n_jobs=-1,
    random_state=RANDOM_STATE,
)

gs_dt.fit(X_train, y_train)

gs_dt_best_score = (
    cross_val_score(
        gs_dt.best_estimator_,
        X_train,
        y_train,
        cv=5,
        scoring="neg_mean_squared_error",
    ).mean()* -1) ** 0.5

gs_dt_best_params = gs_dt.best_params_
gs_dt_fit_time = gs_dt.cv_results_['mean_fit_time'][gs_dt.best_index_]
gs_dt_predict_time = gs_dt.cv_results_['mean_score_time'][gs_dt.best_index_]

print(f"best_params: {gs_dt_best_params}")
print('------------------------------')
print(f"best_score: {gs_dt_best_score}")
print(f"gs_dt_fit_time: {gs_dt_fit_time}")
print(f"gs_dt_predict_time: {gs_dt_predict_time}")

best_params: {'min_samples_split': 3, 'min_samples_leaf': 4, 'max_depth': 5}
------------------------------
best_score: 28.93413347385908
gs_dt_fit_time: 0.041799402236938475
gs_dt_predict_time: 0.003000640869140625
CPU times: total: 203 ms
Wall time: 467 ms


#### CatBoostRegressor

In [25]:
%%time

model_cbr = CatBoostRegressor(random_state=RANDOM_STATE)
param_grid_cbr = {
    "n_estimators": range(50, 251, 50),
    "max_depth": range(2, 15),
    "learning_rate": (0.1, 0.5, 0.8),
    "verbose": (0, 1),
}

gs_cbr = RandomizedSearchCV(
    model_cbr,
    param_distributions=param_grid_cbr,
    scoring="neg_root_mean_squared_error",
    n_jobs=-1,
    random_state=RANDOM_STATE,
)

gs_cbr.fit(X_train, y_train)

gs_cbr_best_score = (
    cross_val_score(
        gs_cbr.best_estimator_,
        X_train,
        y_train,
        cv=5,
        scoring="neg_mean_squared_error",
        n_jobs=-1,
    ).mean()* -1) ** 0.5

gs_cbr_best_params = gs_cbr.best_params_
gs_cbr_fit_time = gs_cbr.cv_results_['mean_fit_time'][gs_cbr.best_index_]
gs_cbr_predict_time = gs_cbr.cv_results_['mean_score_time'][gs_cbr.best_index_]

print(f"best_params: {gs_cbr_best_params}")
print('------------------------------')
print(f"best_score: {gs_cbr_best_score}")
print(f"gs_cbr_fit_time: {gs_cbr_fit_time}")
print(f"gs_cbr_predict_time: {gs_cbr_predict_time}")

0:	learn: 36.9648541	total: 140ms	remaining: 27.8s
1:	learn: 35.3304909	total: 144ms	remaining: 14.2s
2:	learn: 33.9460791	total: 147ms	remaining: 9.65s
3:	learn: 32.7506913	total: 151ms	remaining: 7.39s
4:	learn: 31.7515029	total: 154ms	remaining: 6.01s
5:	learn: 30.8072960	total: 158ms	remaining: 5.1s
6:	learn: 29.9430168	total: 161ms	remaining: 4.44s
7:	learn: 29.3254514	total: 165ms	remaining: 3.95s
8:	learn: 28.6462032	total: 168ms	remaining: 3.57s
9:	learn: 28.1240541	total: 171ms	remaining: 3.26s
10:	learn: 27.5963191	total: 175ms	remaining: 3.01s
11:	learn: 27.1330548	total: 179ms	remaining: 2.8s
12:	learn: 26.7402743	total: 182ms	remaining: 2.63s
13:	learn: 26.3433937	total: 186ms	remaining: 2.47s
14:	learn: 25.9791851	total: 189ms	remaining: 2.33s
15:	learn: 25.6478505	total: 193ms	remaining: 2.22s
16:	learn: 25.4216555	total: 196ms	remaining: 2.11s
17:	learn: 25.1592010	total: 200ms	remaining: 2.02s
18:	learn: 24.9592089	total: 204ms	remaining: 1.94s
19:	learn: 24.7201930	to

#### LightGBM

In [26]:
%%time

model_lgbm = LGBMRegressor(random_state=RANDOM_STATE)
param_grid_lgbm = {
    "num_leaves": range(50, 101),
    "max_depth": range(2, 15),
    "learning_rate": (0.1, 0.5, 0.8),
    "feature_fraction": (0.8, 1.0),
}
gs_lgbm = RandomizedSearchCV(
    model_lgbm,
    param_distributions=param_grid_lgbm,
    scoring="neg_root_mean_squared_error",
    n_jobs=-1,
    random_state=RANDOM_STATE,
)
gs_lgbm.fit(X_train, y_train)

gs_lgbm_best_score = (
    cross_val_score(
        gs_lgbm.best_estimator_,
        X_train,
        y_train,
        cv=5,
        scoring="neg_mean_squared_error",
    ).mean()* -1) ** 0.5

gs_lgbm_best_params = gs_lgbm.best_params_
gs_lgbm_fit_time = gs_lgbm.cv_results_['mean_fit_time'][gs_lgbm.best_index_]
gs_lgbm_predict_time = gs_lgbm.cv_results_['mean_score_time'][gs_lgbm.best_index_]

print(f"best_params: {gs_lgbm_best_params}")
print('------------------------------')
print(f"best_score: {gs_lgbm_best_score}")
print(f"gs_lgbm_fit_time: {gs_lgbm_fit_time}")
print(f"gs_lgbm_predict_time: {gs_lgbm_predict_time}")

[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
best_params: {'num_leaves': 50, 'max_depth': 12, 'learning_rate': 0.1, 'feature_fraction': 1.0}
------------------------------
best_score: 24.690239571295617
gs_lgbm_fit_time: 0.4871947765350342
gs_lgbm_predict_time: 0.036802148818969725
CPU times: total: 5.92 s
Wall time: 2.56 s


### Вывод

In [27]:
result_grid = pd.DataFrame(index=['RMSE','fit time', 'predict time'], columns=['Ridge','DecisionTreeRegressor','CatBoostRegressor','LightGBM'])
result_grid['Ridge'] = gs_ridge_best_score, gs_ridge_fit_time, gs_ridge_predict_time
result_grid['DecisionTreeRegressor'] = gs_dt_best_score, gs_dt_fit_time, gs_dt_predict_time
result_grid['CatBoostRegressor'] = gs_cbr_best_score, gs_cbr_fit_time, gs_cbr_predict_time
result_grid['LightGBM'] = gs_lgbm_best_score, gs_lgbm_fit_time, gs_lgbm_predict_time

result_grid

Ridge  DecisionTreeRegressor  CatBoostRegressor   LightGBM
RMSE          26.256635              28.934133          24.396060  24.690240
fit time       0.005199               0.041799          14.013199   0.487195
predict time   0.002599               0.003001           0.060601   0.036802

Мы подготовили выборки и обучили наши модели. Лучшее значение метрики RMSE показала модель CatBoostRegressor. LightGBMRegressor отстала от лидера совсем на чуть-чуть, но показала при этом гораздо более высокую скорость обучения и предсказания. По-этому, если бы в задании требовалась еще и быстрота работы, то LGMB определенно победила бы. При этом стоит отметить, что все выбранные  и обученные модели попали к целевой диапазон метрики, необходимый по заданию текущего исследования.

## Тестирование

In [28]:
cbr_prediction = gs_cbr.predict(X_test)
cbr_rmse_test = mean_squared_error(y_test, cbr_prediction, squared=False)
cbr_rmse_test

43.23432244178773

In [29]:
result = pd.DataFrame({'Target':y_test, 'Prediction':cbr_prediction})

In [30]:
result.iplot(kind='scatter',xTitle='Dates',yTitle='Returns',title='cbr_prediction')

## Вывод

В ходе настоящего исследования мы загрузили и проанализировали данные. Разбили данные на выборки для обучения модели. Определили 4 типа моделей - Ridge, DecisionTree, CatBoostRegressor, LGBMRegressor, для которых нашли лучшие гиперпараметры, время обучения и предсказания. В завершении проанализировали модели, опираясь на значения метрики RMSE, в результате чего можно сделать вывод о том, что наиболее подходящей моделью (из выбранных нами для исследования) для прогнозирования количества заказов такси на следующий час явялется модель **CatBoostRegressor**. По качеству предсказаний ближе всего к ней была LGMBR-модель. Линейная же и "деревянная" же модели, отстали по этому параметру на несколько пунктов.

![gif](https://media.giphy.com/media/qixPSDrFZSM48/giphy.gif)

## Чек-лист проверки

- [x]  Jupyter Notebook открыт
- [x]  Весь код выполняется без ошибок
- [x]  Ячейки с кодом расположены в порядке исполнения
- [x]  Данные загружены и подготовлены
- [x]  Данные проанализированы
- [x]  Модель обучена, гиперпараметры подобраны
- [x]  Качество моделей проверено, выводы сделаны
- [x]  Значение *RMSE* на тестовой выборке не больше 48